Lambda School Data Science

*Unit 4, Sprint 1, Module 4*

---

# Topic Modeling (Prepare)

# Latent Dirchilet Allocation (LDA) Models (Prepare)
<a id="#p1"></a>

## Overview
LDA is a "generative probabilistic model". 

Let's play with a modoel available [here](https://lettier.com/projects/lda-topic-modeling/)

## Follow Along

## Challenge 

# Estimating LDA Models with Gensim (Learn)
<a id="#p1"></a>

## Overview
### A Litterary Introduction: *Jane Austen V. Charlotte Bronte*
Despite being born nearly forty years apart, modern fans often pit Jane Austen & Charlotte Bronte against one another in a battle for litterary  supremacy. The battle centers around the topics of education for women, courting, and marriage. The authors' similiar backgrounds naturally draw comparisons, but the modern fascination is probably due to novelility of British women publishing novels during the early 19th century. 

Can we help close a litterary battle for supremacy and simply acknowledge that the authors addressed different topics and deserve to be acknowledged as excellent authors each in their own right?

We're going to apply Latent Dirichlet Allocation a machine learning alogrithm for topic modeling to each of the author's novels to compare the distribution of topics in their novels.

In [1]:
import numpy as np
import gensim
import os
import re

from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from gensim import corpora

from gensim.models.ldamulticore import LdaMulticore

import pandas as pd

### Novel Data
I grabbed the novel data pre-split into a bunch of smaller chuncks

In [2]:
path = './data/austen-brontë-split'

In [8]:
STOPWORDS = set(STOPWORDS).union(set(['said', 'mr', 'mrs']))

def tokenize(text):
    return [token for token in simple_preprocess(text) if token not in STOPWORDS]

In [21]:
import os

def gather_data(path_to_data): 
    data = []
    for f in os.listdir(path):
        if os.path.isdir(f) == False:
            if f[-3:] == 'txt':
                with open(os.path.join(path,f)) as t:
                    text = t.read().strip('\n')
                    data.append(tokenize(str(text)))       
    return data

In [22]:
tokens = gather_data(path)

In [14]:
"this is a sample string with a \n newline character".replace('\n', '')

'this is a sample string with a  newline character'

In [18]:
df.head(0)

Empty DataFrame
Columns: [tokens]
Index: []

## Follow Along

### Text Preprocessing
**Challenge**: update the function `tokenize` with any technique you have learned so far this week. 

In [19]:
titles = [t[:-4] for t in os.listdir(path)]

In [20]:
titles[:5]

['CBronte_Professor0080',
 'CBronte_Jane0164',
 'Austen_Emma0025',
 'Austen_Pride0036',
 'Austen_Emma0077']

In [23]:
df = pd.DataFrame(index=titles, data={'tokens': tokens})

In [24]:
STOPWORDS = set(STOPWORDS).union(set(['said', 'mr', 'mrs']))

def tokenize(text):
    return [token for token in simple_preprocess(text) if token not in STOPWORDS]

In [7]:
tokenize("Hello World! This a test of the tokenization method")

['hello', 'world', 'test', 'tokenization', 'method']

### Author DataFrame


In [9]:
df = pd.DataFrame(index=titles)

In [10]:
df.head()

Empty DataFrame
Columns: []
Index: [Austen_Emma0026, Austen_Emma0032, CBronte_Villette0086, CBronte_Jane0099, CBronte_Villette0092]

In [14]:
#

ValueError: invalid literal for int() with base 10: 'ckpo'

In [25]:
df.head()

tokens
CBronte_Professor0080  [piece, hall, stag, heard, brown, madame, vand...
CBronte_Jane0164       [receive, oh, st, john, cried, mercy, appealed...
Austen_Emma0025        [important, variation, draw, shall, read, musi...
Austen_Pride0036       [circumstances, favour, attachment, prevent, w...
Austen_Emma0077        [dear, highbury, friendly, shake, hand, earnes...

In [26]:
df['author'] = df.reset_index()['index'].apply(lambda x: x.split('_')[0]).tolist()
df['book'] = df.reset_index()['index'].apply(lambda x: x.split('_')[1][:-4]).tolist()
df['section'] = df.reset_index()['index'].apply(lambda x: x[-4:]).tolist()
df['section'] = df['section'].astype('int')

In [27]:
df['author'] = df['author'].map({'Austen':1, 'CBronte':0})

In [28]:
df.author.value_counts()

0    441
1    372
Name: author, dtype: int64

### Streaming Documents
Here we use a new pythonic thingy: the `yield` statement in our fucntion. This allows us to iterate over a bunch of documents without actually reading them into memory. You can see how we use this fucntion later on. 

In [29]:
def doc_stream(path):
    for f in os.listdir(path):
        if os.path.isdir(f) == False:
            if f[-3:] == 'txt':
                with open(os.path.join(path,f)) as t:
                    text = t.read().strip('\n')
                    tokens = tokenize(str(text))
                yield tokens

In [30]:
streaming_data = doc_stream(path)

In [29]:
print()

### Gensim LDA Topic Modeling

In [31]:
# A Dictionary Representation of all the words in our corpus
id2word = corpora.Dictionary(doc_stream(path))

In [32]:
id2word.token2id['england']

136

In [33]:
id2word.doc2bow(tokenize("This is a sample message Darcy England England England"))

[(136, 3), (647, 1), (1483, 1), (8990, 1)]

In [34]:
import sys
sys.getsizeof(id2word)

56

In [35]:
len(id2word.keys())

22096

In [36]:
# Let's remove extreme values from the dataset
id2word.filter_extremes(no_below=10, no_above=0.75)

In [37]:
len(id2word.keys())

4922

In [38]:
# a bag of words(bow) representation of our corpus
# Note: we haven't actually read any text into memory here
corpus = [id2word.doc2bow(text) for text in doc_stream(path)]

In [39]:
lda = LdaMulticore(corpus=corpus,
                   id2word=id2word,
                   random_state=723812,
                   num_topics = 15,
                   passes=10,
                   workers=4
                  )

In [40]:
lda.print_topics()

[(0,
  '0.019*"elinor" + 0.017*"marianne" + 0.008*"sister" + 0.007*"willoughby" + 0.007*"jennings" + 0.007*"edward" + 0.006*"mother" + 0.006*"dashwood" + 0.006*"know" + 0.005*"lucy"'),
 (1,
  '0.006*"like" + 0.005*"madame" + 0.005*"thought" + 0.004*"day" + 0.004*"long" + 0.004*"know" + 0.003*"eyes" + 0.003*"hand" + 0.003*"looked" + 0.003*"saw"'),
 (2,
  '0.009*"john" + 0.008*"st" + 0.008*"like" + 0.007*"school" + 0.006*"diana" + 0.006*"house" + 0.005*"bessie" + 0.005*"long" + 0.005*"thought" + 0.005*"think"'),
 (3,
  '0.013*"edward" + 0.011*"colonel" + 0.011*"elinor" + 0.011*"ferrars" + 0.009*"house" + 0.007*"brandon" + 0.007*"fanny" + 0.006*"think" + 0.005*"living" + 0.005*"sir"'),
 (4,
  '0.015*"miss" + 0.009*"like" + 0.006*"shall" + 0.006*"know" + 0.006*"rochester" + 0.005*"lady" + 0.005*"sir" + 0.005*"think" + 0.005*"ingram" + 0.005*"yes"'),
 (5,
  '0.010*"st" + 0.010*"john" + 0.006*"like" + 0.006*"mary" + 0.006*"diana" + 0.005*"moment" + 0.004*"long" + 0.004*"rochester" + 0.004*"l

In [41]:
words = [re.findall(r'"([^"]*)"',t[1]) for t in lda.print_topics()]

In [42]:
topics = [' '.join(t[0:5]) for t in words]

In [47]:
for id, t in enumerate(topics): 
    print(f' ------- Topic {id} --------')
    print(t, end='\n\n')

 ------- Topic 0 --------
elinor marianne sister willoughby jennings

 ------- Topic 1 --------
like madame thought day long

 ------- Topic 2 --------
john st like school diana

 ------- Topic 3 --------
edward colonel elinor ferrars house

 ------- Topic 4 --------
miss like shall know rochester

 ------- Topic 5 --------
st john like mary diana

 ------- Topic 6 --------
elizabeth gardiner master darcy brother

 ------- Topic 7 --------
emma miss harriet weston elton

 ------- Topic 8 --------
monsieur frances like lucy think

 ------- Topic 9 --------
bretton graham dr lucy know

 ------- Topic 10 --------
man miss think father young

 ------- Topic 11 --------
saw rosine dr john doctor

 ------- Topic 12 --------
man like hunsden face coffee

 ------- Topic 13 --------
elizabeth darcy bennet bingley jane

 ------- Topic 14 --------
jane room like night rochester



## Challenge 

You will apply an LDA model to a customer review dataset to practice the fitting and estimation of LDA. 

# Interpret LDA Results (Learn)
<a id="#p3"></a>

## Overview

## Follow Along

### Topic Distance Visualization

In [48]:
import pyLDAvis.gensim

pyLDAvis.enable_notebook()

/home/jay/anaconda3/envs/nlp-u4-s1/lib/python3.7/site-packages/past/types/oldstr.py:5: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated, and in 3.8 it will stop working
  from collections import Iterable


In [49]:
pyLDAvis.gensim.prepare(lda, corpus, id2word)

/home/jay/anaconda3/envs/nlp-u4-s1/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1     -0.092086 -0.004601       1        1  25.579515
7      0.098365  0.007432       2        1  14.484544
14    -0.078976  0.051797       3        1  13.830023
13     0.107081 -0.010234       4        1  13.305294
0      0.094012 -0.011827       5        1  11.201076
10     0.132696 -0.028713       6        1   4.793737
4     -0.003978  0.028151       7        1   4.188620
9     -0.012085  0.019896       8        1   3.863658
5     -0.097697  0.101055       9        1   2.722178
8     -0.090465 -0.005935      10        1   2.397407
3      0.113070 -0.015043      11        1   1.290168
2     -0.023879  0.081204      12        1   1.199387
6      0.049404  0.004293      13        1   0.822614
11    -0.123748 -0.124416      14        1   0.189265
12    -0.071714 -0.093060      15        1   0.132517, topic_info=     Category         Freq        Term        Total  loglift  logprob
557   Default   632.000000   elizabeth   632.000000  30.0000  30.0000
22    Default  1328.000000        like  1328.000000  29.0000  29.0000
1022  Default   673.000000      elinor   673.000000  28.0000  28.0000
344   Default   875.000000        emma   875.000000  27.0000  27.0000
1075  Default   560.000000    marianne   560.000000  26.0000  26.0000
254   Default  1316.000000       think  1316.000000  25.0000  25.0000
408   Default  1535.000000        miss  1535.000000  24.0000  24.0000
141   Default   616.000000        john   616.000000  23.0000  23.0000
540   Default   409.000000       darcy   409.000000  22.0000  22.0000
160   Default   909.000000         man   909.000000  21.0000  21.0000
587   Default   748.000000       house   748.000000  20.0000  20.0000
214   Default   779.000000         saw   779.000000  19.0000  19.0000
20    Default  1442.000000        know  1442.000000  18.0000  18.0000
1304  Default   498.000000        face   498.000000  17.0000  17.0000
478   Default  1150.000000     thought  1150.000000  16.0000  16.0000
27    Default   271.000000    monsieur   271.000000  15.0000  15.0000
373   Default   530.000000     harriet   530.000000  14.0000  14.0000
832   Default   446.000000      weston   446.000000  13.0000  13.0000
1019  Default   306.000000      edward   306.000000  12.0000  12.0000
620   Default   627.000000       night   627.000000  11.0000  11.0000
1294  Default   235.000000          dr   235.000000  10.0000  10.0000
140   Default   941.000000        jane   941.000000   9.0000   9.0000
87    Default  1068.000000         day  1068.000000   8.0000   8.0000
1072  Default   373.000000        lucy   373.000000   7.0000   7.0000
1273  Default   244.000000     bretton   244.000000   6.0000   6.0000
343   Default   391.000000       elton   391.000000   5.0000   5.0000
855   Default   300.000000     colonel   300.000000   4.0000   4.0000
764   Default   394.000000   knightley   394.000000   3.0000   3.0000
25    Default   414.000000      madame   414.000000   2.0000   2.0000
169   Default   577.000000      moment   577.000000   1.0000   1.0000
...       ...          ...         ...          ...      ...      ...
9     Topic15     2.068587  crimsworth    97.346985   2.7748  -5.2134
2204  Topic15     2.626810     hunsden   146.966522   2.6018  -4.9745
3046  Topic15     1.055476        cast    55.936378   2.6560  -5.8863
1675  Topic15     1.086491         lie    62.136627   2.5798  -5.8573
1304  Topic15     2.612887        face   498.856476   1.3744  -4.9798
1370  Topic15     1.064570   perceived    78.991791   2.3194  -5.8777
160   Topic15     2.728398         man   909.724365   0.8168  -4.9366
2724  Topic15     1.081730   surprised   101.574745   2.0840  -5.8617
22    Topic15     2.723191        like  1328.896729   0.4359  -4.9385
556   Topic15     1.074398      effect   119.649506   1.9134  -5.8685
254   Topic15     2.307720       think  1316.210693   0.2800  -5.1040
681   Topic15     1.062862   

### Overall Model / Documents

In [50]:
lda[corpus[0]]

[(1, 0.7680385), (4, 0.16803199), (9, 0.047262773)]

In [51]:
distro = [lda[d] for d in corpus]

In [52]:
distro[0]

[(1, 0.7681098), (4, 0.16794124), (9, 0.04728225)]

In [53]:
distro = [lda[d] for d in corpus]

def update(doc):
        d_dist = {k:0 for k in range(0,15)}
        for t in doc:
            d_dist[t[0]] = t[1]
        return d_dist
    
new_distro = [update(d) for d in distro]

In [55]:
df.head()

tokens  \
CBronte_Professor0080  [piece, hall, stag, heard, brown, madame, vand...   
CBronte_Jane0164       [receive, oh, st, john, cried, mercy, appealed...   
Austen_Emma0025        [important, variation, draw, shall, read, musi...   
Austen_Pride0036       [circumstances, favour, attachment, prevent, w...   
Austen_Emma0077        [dear, highbury, friendly, shake, hand, earnes...   

                       author       book  section  
CBronte_Professor0080       0  Professor       80  
CBronte_Jane0164            0       Jane      164  
Austen_Emma0025             1       Emma       25  
Austen_Pride0036            1      Pride       36  
Austen_Emma0077             1       Emma       77

In [56]:
df = pd.DataFrame.from_records(new_distro, index=titles)
df.columns = topics
df['author'] = df.reset_index()['index'].apply(lambda x: x.split('_')[0]).tolist()

In [57]:
df.head()

elinor marianne sister willoughby jennings  \
CBronte_Professor0080                                    0.000000   
CBronte_Jane0164                                         0.000000   
Austen_Emma0025                                          0.227373   
Austen_Pride0036                                         0.000000   
Austen_Emma0077                                          0.000000   

                       like madame thought day long  \
CBronte_Professor0080                      0.766462   
CBronte_Jane0164                           0.434480   
Austen_Emma0025                            0.000000   
Austen_Pride0036                           0.000000   
Austen_Emma0077                            0.000000   

                       john st like school diana  \
CBronte_Professor0080                        0.0   
CBronte_Jane0164                             0.0   
Austen_Emma0025                              0.0   
Austen_Pride0036                             0.0   
Austen_Emma0077                              0.0   

                       edward colonel elinor ferrars house  \
CBronte_Professor0080                                  0.0   
CBronte_Jane0164                                       0.0   
Austen_Emma0025                                        0.0   
Austen_Pride0036                                       0.0   
Austen_Emma0077                                        0.0   

                       miss like shall know rochester  \
CBronte_Professor0080                        0.170479   
CBronte_Jane0164                             0.000000   
Austen_Emma0025                              0.000000   
Austen_Pride0036                             0.000000   
Austen_Emma0077                              0.000000   

                       st john like mary diana  \
CBronte_Professor0080                 0.000000   
CBronte_Jane0164                      0.329076   
Austen_Emma0025                       0.000000   
Austen_Pride0036                      0.000000   
Austen_Emma0077                       0.000000   

                       elizabeth gardiner master darcy brother  \
CBronte_Professor0080                                      0.0   
CBronte_Jane0164                                           0.0   
Austen_Emma0025                                            0.0   
Austen_Pride0036                                           0.0   
Austen_Emma0077                                            0.0   

                       emma miss harriet weston elton  \
CBronte_Professor0080                        0.000000   
CBronte_Jane0164                             0.000000   
Austen_Emma0025                              0.453120   
Austen_Pride0036                             0.000000   
Austen_Emma0077                              0.642444   

                       monsieur frances like lucy think  \
CBronte_Professor0080                               0.0   
CBronte_Jane0164                                    0.0   
Austen_Emma0025                                     0.0   
Austen_Pride0036                                    0.0   
Austen_Emma0077                                     0.0   

                       bretton graham dr lucy know  \
CBronte_Professor0080                     0.046392   
CBronte_Jane0164                          0.000000   
Austen_Emma0025                           0.000000   
Austen_Pride0036                          0.000000   
Austen_Emma0077                           0.000000   

                       man miss think father young  saw rosine dr john doctor  \
CBronte_Professor0080                     0.000000                        0.0   
CBronte_Jane0164                          0.017552                        0.0   
Austen_Emma0025                           0.297451                        0.0   
Austen_Pride0036                          0.000000                        0.0   
Austen_Emma0077                           0.139940                        0.0   

                       man like hunsden 

In [58]:
df.groupby('author').mean()

elinor marianne sister willoughby jennings  \
author                                                
Austen                                     0.231545   
CBronte                                    0.004981   

         like madame thought day long  john st like school diana  \
author                                                             
Austen                       0.008119                   0.000739   
CBronte                      0.447518                   0.022700   

         edward colonel elinor ferrars house  miss like shall know rochester  \
author                                                                         
Austen                              0.025272                        0.013190   
CBronte                             0.001653                        0.070501   

         st john like mary diana  elizabeth gardiner master darcy brother  \
author                                                                      
Austen                  0.000000                                 0.015658   
CBronte                 0.053146                                 0.003003   

         emma miss harriet weston elton  monsieur frances like lucy think  \
author                                                                      
Austen                         0.307341                          0.000000   
CBronte                        0.002537                          0.042279   

         bretton graham dr lucy know  man miss think father young  \
author                                                              
Austen                      0.001260                     0.093439   
CBronte                     0.067596                     0.009462   

         saw rosine dr john doctor  man like hunsden face coffee  \
author                                                             
Austen                    0.000000                      0.000000   
CBronte                   0.003065                      0.002261   

         elizabeth darcy bennet bingley jane  jane room like night rochester  
author                                                                        
Austen                              0.295828                        0.004823  
CBronte                             0.007695                        0.258924

## Challenge
### *Can we see if one of the authors focus more on men than women?*

*  Use Spacy for text prepocessing
*  Extract the Named Entities from the documents using Spacy (command is fairly straight forward)
*  Create unique list of names from the authors (you'll find that there are different types of named entities not all people)
*  Label the names with genders (can you this by hand or you use the US census name lists)
*  Customize your processing to replace the proper name with your gender from the previous step's lookup table
*  Then follow the rest of the LDA flow


# Selecting the Number of Topics (Learn)
<a id="#p4"></a>

## Overview

## Follow Along

In [59]:
from gensim.models.coherencemodel import CoherenceModel

def compute_coherence_values(dictionary, corpus, path, limit, start=2, step=3, passes=5):
    """
    Compute c_v coherence for various number of topics

    Parameters:
    ----------
    dictionary : Gensim dictionary
    corpus : Gensim corpus
    path : path to input texts
    limit : Max num of topics
    passes: the number of times the entire lda model & coherence values are calculated

    Returns:
    -------
    coherence_values : Coherence values corresponding to the LDA model with respective number of topics
    """
    
    coherence_values = []
    
    tokens = list(doc_stream(path))
    
    for iter_ in range(passes):
        for num_topics in range(start, limit, step):
            stream = doc_stream(path)
            model = LdaMulticore(corpus=corpus, num_topics=num_topics, id2word=dictionary, workers=4)
            coherencemodel = CoherenceModel(model=model,dictionary=dictionary,corpus=corpus, coherence='u_mass')
            coherence_values.append({'pass': iter_, 
                                     'num_topics': num_topics, 
                                     'coherence_score': coherencemodel.get_coherence()
                                    })

    return coherence_values

In [ ]:
# Can take a long time to run.
coherence_values = compute_coherence_values(dictionary=id2word, 
                                                        corpus=corpus, 
                                                        path=path, 
                                                        start=2, 
                                                        limit=40, 
                                                        step=6,
                                                        passes=40)

/home/jay/anaconda3/envs/nlp-u4-s1/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/jay/anaconda3/envs/nlp-u4-s1/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/jay/anaconda3/envs/nlp-u4-s1/lib/python3.7/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.from_iter(generator)) or the python sum builtin instead.


In [123]:
topic_coherence = pd.DataFrame.from_records(coherence_values)

NameError: name 'coherencemodel' is not defined

In [124]:
topic_coherence.head()

coherence_score  num_topics  pass
0        -0.935416           2     0
1        -0.939436           8     0
2        -0.952264          14     0
3        -0.912855          20     0
4        -0.905050          26     0

In [125]:
import seaborn as sns

ax = sns.lineplot(x="num_topics", y="coherence_score", data=topic_coherence)

In [76]:
# Print the coherence scores
for m, cv in zip(x, coherence_values):
    print("Num Topics =", m, " has Coherence Value of", round(cv, 4))

Num Topics = 2  has Coherence Value of 0.2785
Num Topics = 8  has Coherence Value of 0.3029
Num Topics = 14  has Coherence Value of 0.2887
Num Topics = 20  has Coherence Value of 0.2852
Num Topics = 26  has Coherence Value of 0.2846
Num Topics = 32  has Coherence Value of 0.2914
Num Topics = 38  has Coherence Value of 0.2878


In [89]:
lda[id2word.doc2bow(tokenize("This is a sample document to score with a topic distribution."))]

[(0, 0.02226036),
 (1, 0.022260414),
 (2, 0.022260347),
 (3, 0.022260347),
 (4, 0.022260392),
 (5, 0.0222604),
 (6, 0.022260347),
 (7, 0.35487327),
 (8, 0.022260398),
 (9, 0.022260517),
 (10, 0.022260416),
 (11, 0.022260422),
 (12, 0.3557417),
 (13, 0.022260347),
 (14, 0.022260347)]

## Challenge
### *Can we see if one of the authors focus more on men than women?*

*  Use Spacy for text prepocessing
*  Extract the Named Entities from the documents using Spacy (command is fairly straight forward)
*  Create unique list of names from the authors (you'll find that there are different types of named entities not all people)
*  Label the names with genders (can you this by hand or you use the US census name lists)
*  Customize your processing to replace the proper name with your gender from the previous step's lookup table
*  Then follow the rest of the LDA flow

In [78]:
import spacy

nlp = spacy.load('en_core_web_lg')

/Users/jonathansokoll/anaconda3/envs/U4-S1-NLP/lib/python3.7/site-packages/thinc/neural/train.py:7: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated, and in 3.8 it will stop working
  from .optimizers import Adam, linear_decay
/Users/jonathansokoll/anaconda3/envs/U4-S1-NLP/lib/python3.7/site-packages/thinc/check.py:4: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated, and in 3.8 it will stop working
  from collections import Sequence, Sized, Iterable, Callable
/Users/jonathansokoll/anaconda3/envs/U4-S1-NLP/lib/python3.7/site-packages/thinc/check.py:4: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated, and in 3.8 it will stop working
  from collections import Sequence, Sized, Iterable, Callable


In [79]:
test = "Ned asked me a question about England today."

In [80]:
doc = nlp(test)

for token in doc:
    print(token.text, token.lemma_, token.pos_)

Ned Ned PROPN
asked ask VERB
me -PRON- PRON
a a DET
question question NOUN
about about ADP
England England PROPN
today today NOUN
. . PUNCT


In [81]:
for ent in doc.ents:
    print(ent.text, ent.label_)

Ned PERSON
England GPE
today DATE


In [82]:
def doc_stream(path):
    for f in os.listdir(path):
        with open(os.path.join(path,f)) as t:
            text = t.read().strip('\n')
            yield text

def get_people(docstream):
    
    ppl = []
    
    for d in docstream:
        
        doc = nlp(d)
        
        for ent in doc.ents:
            
            if ent.label_ == "PERSON":
                ppl.append(ent.lemma_)
                
    return set(ppl)

In [129]:
people = get_people(doc_stream(path))

In [126]:
doc = nlp(next(doc_stream(path)))

In [128]:
doc.ents[0].lemma_

'yesterday'

# Sources

### *References*
* [Andrew Ng et al paper on LDA](https://ai.stanford.edu/~ang/papers/jair03-lda.pdf)
* On [Coherence](https://pdfs.semanticscholar.org/1521/8d9c029cbb903ae7c729b2c644c24994c201.pdf)

### *Resources*

* [Gensim](https://radimrehurek.com/gensim/): Python package for topic modeling, nlp, word vectorization, and few other things. Well maintained and well documented.
* [Topic Modeling with Gensim](http://www.machinelearningplus.com/nlp/topic-modeling-gensim-python/#11createthedictionaryandcorpusneededfortopicmodeling): A kind of cookbook for LDA with gensim. Excellent overview, but the you need to be aware of missing import statements and assumed prior knowledge.
* [Chinese Restuarant Process](https://en.wikipedia.org/wiki/Chinese_restaurant_process): That really obscure stats thing I mentioned... 
* [PyLDAvis](https://github.com/bmabey/pyLDAvis): Library for visualizing the topic model and performing some exploratory work. Works well. Has a direct parrell implementation in R as well. 
* [Rare Technologies](https://rare-technologies.com/): The people that made & maintain gensim and a few other libraries.
* [Jane Austen v. Charlotte Bronte](https://www.literaryladiesguide.com/literary-musings/jane-austen-charlotte-bronte-different-alike/)